In [1]:
import itertools
import multiprocessing as mp
import os

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from IPython.core.display_functions import display
from sklearn import preprocessing
import sklearn.metrics as metrics
from shared_logic import *
import plotly.express as px
random_seed = 1
np.random.seed(random_seed)


In [2]:
plt.style.use('seaborn-colorblind')

# from https://jwalton.info/Embed-Publication-Matplotlib-Latex/
tex_fonts = {
    # Use LaTeX to write all text
    "text.usetex": True,
    "font.family": "serif",
    # Use 11pt font in plots, to match 11pt font in document
    "axes.labelsize": 11,
    "font.size": 11
}
plt.rcParams.update(tex_fonts)


In [3]:
stations_df = pd.read_csv('./data/stations.csv')
stations_dict = stations_df.groupby(['common_id']).first().to_dict('index')
common_id = '36022-ie'
# common_id = '39003-ie'
# common_id = '2386-ch'
# common_id = '42960105-de'
# common_id = '2720050000-de'
tex_plots_path = f'../bachelor-thesis/plots/pdfs/{common_id}/'
tex_table_path = f'../bachelor-thesis/tables/{common_id}/'

df = pd.read_parquet(f'data/classified_raw/{common_id}_outliers_classified.parquet')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27189 entries, 0 to 27188
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype              
---  ------       --------------  -----              
 0   water_level  27189 non-null  float64            
 1   timestamp    27189 non-null  datetime64[ns, UTC]
 2   is_outlier   27189 non-null  bool               
dtypes: bool(1), datetime64[ns, UTC](1), float64(1)
memory usage: 451.5 KB


In [4]:
df['is_outlier'].value_counts()

False    26544
True       645
Name: is_outlier, dtype: int64

In [5]:
df.head(9).to_latex(
    f'{tex_table_path}/{common_id}-9head.tex', position='htp', index=False,
    label=f'table:{common_id}-9head',
    caption=f'First 9 values of {stations_dict[common_id]["water_name"]} - {stations_dict[common_id]["station_name"]}')

/tmp/ipykernel_94389/707070294.py:1: FutureWarning: In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.
  df.head(9).to_latex(


In [6]:
display(df.describe())
display(df.loc[df['is_outlier']].describe())
display(df.loc[~df['is_outlier']].describe())


water_level
count  27189.000000
mean      36.009754
std       14.716286
min        0.000000
25%       26.400000
50%       31.700000
75%       40.300000
max      190.000000

water_level
count   645.000000
mean     61.876744
std      25.476859
min       0.000000
25%      40.000000
50%      60.000000
75%      80.000000
max     190.000000

water_level
count  26544.000000
mean      35.381205
std       13.763332
min       20.000000
25%       26.400000
50%       31.400000
75%       39.800000
max      151.600000

In [7]:
import outlier_detection_methods as odm

In [10]:
threshold = 7.6
median_od_df = odm.median_outlier_detection(df, 5, True)
median_od_df['is_outlier_pred'] = np.where(median_od_df['result'].to_numpy() > threshold, True, False)
mean_threshold_confusion_matrix = metrics.confusion_matrix(median_od_df['is_outlier'], median_od_df['is_outlier_pred'])
print('TP, FN\nFP, TN')
print(mean_threshold_confusion_matrix)
print(metrics.f1_score(median_od_df['is_outlier'], median_od_df['is_outlier_pred']))


TP, FN
FP, TN
[[26451    93]
 [  140   505]]
0.8125502815768301


In [57]:
window_size = 13
center_window = False
threshold = 50
mean_threshold_df = df.copy()
if window_size is not None:
    mean_threshold_df['x_hat'] = mean_threshold_df['water_level'].rolling(window=window_size, center=center_window, min_periods=1).mean()
else:
    mean_threshold_df['x_hat'] = mean_threshold_df['water_level'].mean()
mean_threshold_df['abs_diff'] = (mean_threshold_df['x_hat'] - mean_threshold_df['water_level']).abs()
mean_threshold_df['is_outlier_pred'] = np.where(mean_threshold_df['abs_diff'].to_numpy() > threshold, True, False)
mean_threshold_confusion_matrix = metrics.confusion_matrix(mean_threshold_df['is_outlier'], mean_threshold_df['is_outlier_pred'])
print('TP, FN\nFP, TN')
print(mean_threshold_confusion_matrix)
print(metrics.f1_score(mean_threshold_df['is_outlier'], mean_threshold_df['is_outlier_pred']))


TP, FN
FP, TN
[[26500    44]
 [  549    96]]
0.2445859872611465


In [6]:

x_norm = preprocessing.normalize(df['water_level'].values.reshape(-1, 1))
X = df['water_level'].values.reshape(-1, 1)
y = df['is_outlier'].astype(int).to_numpy().reshape(-1, 1)
x_hats = {}

In [7]:
def get_x_hat(X: np.ndarray, method: str, window: int = None,
              center_window: bool = False) -> np.ndarray:
    if window is None:
        if method == 'mean':
            return np.full(X.shape, X.mean())
        elif method == 'median':
            return np.full(X.shape, np.median(X))
        elif method == 'mad':
            return np.full(X.shape, np.median(np.abs(X - np.median(X))))
        else:
            raise ValueError(f'Method {method} not supported')
    else:
        if method == 'mean':
            tmp_df = pd.DataFrame({'X': X.reshape(-1)})
            return tmp_df['X'].rolling(window=window, min_periods=1,
                                       center=center_window).mean().to_numpy().reshape(
                -1, 1)
        elif method == 'median':
            tmp_df = pd.DataFrame({'X': X.reshape(-1)})
            return tmp_df['X'].rolling(window=window, min_periods=1,
                                       center=center_window).median().to_numpy().reshape(
                -1, 1)
        elif method == 'mad':
            tmp_df = pd.DataFrame({'X': X.reshape(-1)})
            return tmp_df['X'].rolling(window=window, min_periods=1,
                                       center=center_window).apply(
                lambda x: np.median(
                    np.abs(x - np.median(x)))).to_numpy().reshape(-1, 1)
        else:
            raise ValueError(f'Method {method} not supported')

In [8]:
def get_TP_TN_FP_FN(actual, predicted):
    if actual == True and predicted == True:
        return 'TP'
    elif actual == False and predicted == False:
        return 'TN'
    elif actual == False and predicted == True:
        return 'FP'
    elif actual == True and predicted == False:
        return 'FN'
    else:
        raise ValueError(f'Invalid actual and predicted values: {actual} {predicted}')

In [9]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
mad_norm_df = df.copy()
mad_norm_df['water_level_norm'] = scaler.fit_transform(mad_norm_df[['water_level']])
window_size = 20
center_window = True
mad_norm_df['Median'] = mad_norm_df['water_level_norm'].rolling(window=window_size, min_periods=1, center=center_window).median()
mad_norm_df['MAD'] = mad_norm_df['water_level_norm'].rolling(window=window_size, min_periods=1, center=center_window).apply(lambda x: np.median(np.abs(x - np.median(x))))
mad_norm_df['MADN'] = mad_norm_df['MAD'] / 0.6745
mad_norm_df['M'] = mad_norm_df.apply(lambda row: np.abs(row['water_level_norm'] - row['Median']) / row['MADN'] if row['MADN'] != 0 else 0, axis=1)
mad_norm_df['prediction'] = mad_norm_df.apply(lambda row: True if row['M'] > 15 else False, axis=1)
print(f"f1: {metrics.f1_score(mad_norm_df['is_outlier'], mad_norm_df['prediction'])}")
print(f"precision {metrics.precision_score(mad_norm_df['is_outlier'], mad_norm_df['prediction'])}")
print(f"recall {metrics.recall_score(mad_norm_df['is_outlier'], mad_norm_df['prediction'])}")
# f1: 0.6761800219538967
# precision 0.9935483870967742
# recall 0.5124792013311148
mad_norm_df['cn'] = mad_norm_df.apply(lambda row: get_TP_TN_FP_FN(row['is_outlier'], row['prediction']), axis=1)
fig = px.scatter(mad_norm_df, x='timestamp', y='water_level_norm', color='cn',
           title='Water level')
# fig.show()
fig = px.scatter(mad_norm_df, x='timestamp', y='M', color='cn',
           title='Water level')
# fig.show()

# mad_norm_df

f1: 0.6724700761697499
precision 0.9967741935483871
recall 0.5073891625615764


In [30]:
scaler = StandardScaler()
mad_df = df.copy()
mad_df['water_level_norm'] = scaler.fit_transform(mad_df[['water_level']])
window_size = 20
center_window = True
mad_df['Median'] = mad_df['water_level'].rolling(window=window_size, min_periods=1, center=center_window).median()
mad_df['MAD'] = mad_df['water_level'].rolling(window=window_size, min_periods=1, center=center_window).apply(lambda x: np.median(np.abs(x - np.median(x))))
mad_df['MADN'] = mad_df['MAD'] / 0.6745
mad_df['M'] = mad_df.apply(lambda row: np.abs(row['water_level'] - row['Median']) / row['MADN'] if row['MADN'] != 0 else 0, axis=1)
mad_df['prediction'] = mad_df.apply(lambda row: True if row['M'] > 7 else False, axis=1)
print(metrics.f1_score(mad_df['is_outlier'], mad_df['prediction']))
mad_df['cn'] = mad_df.apply(lambda row: get_TP_TN_FP_FN(row['is_outlier'], row['prediction']), axis=1)
fig = px.scatter(mad_df, x='timestamp', y='water_level', color='cn',
           title='Water level')
# fig.show()
fig = px.scatter(mad_df, x='timestamp', y='M', color='cn',
           title='Water level')
# fig.show()
# mad_df

0.8146718146718147


water_level                 timestamp  is_outlier  water_level_norm  \
index                                                                        
0             24.9 2019-06-30 15:00:00+00:00       False         -0.761236   
1             24.9 2019-06-30 16:00:00+00:00       False         -0.761236   
2             24.8 2019-06-30 17:00:00+00:00       False         -0.768072   
3             24.4 2019-06-30 18:00:00+00:00       False         -0.795417   
4             24.4 2019-06-30 19:00:00+00:00       False         -0.795417   
...            ...                       ...         ...               ...   
27184         22.1 2022-04-02 12:15:00+00:00       False         -0.952649   
27185         22.6 2022-04-02 12:45:00+00:00       False         -0.918468   
27186         22.3 2022-04-02 13:15:00+00:00       False         -0.938977   
27187         22.4 2022-04-02 13:45:00+00:00       False         -0.932141   
27188         22.8 2022-04-02 14:00:00+00:00       False         -0.904796   

       Median  MAD      MADN         M  prediction  cn  
index                                                   
0       24.40  0.4  0.593032  0.843125       False  TN  
1       24.40  0.4  0.593032  0.843125       False  TN  
2       24.35  0.5  0.741290  0.607050       False  TN  
3       24.30  0.6  0.889548  0.112417       False  TN  
4       24.20  0.6  0.889548  0.224833       False  TN  
...       ...  ...       ...       ...         ...  ..  
27184   22.00  0.2  0.296516  0.337250       False  TN  
27185   22.00  0.2  0.296516  2.023500       False  TN  
27186   22.00  0.2  0.296516  1.011750       False  TN  
27187   22.00  0.2  0.296516  1.349000       False  TN  
27188   22.00  0.2  0.296516  2.698000       False  TN  

[27153 rows x 10 columns]

In [ ]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
median_norm_df = df.copy()
median_norm_df['water_level_norm'] = scaler.fit_transform(median_norm_df[['water_level']])
window_size = 10
center_window = True
median_norm_df['Median'] = median_norm_df['water_level_norm'].rolling(window=window_size, min_periods=1, center=center_window).median()
# median_norm_df['MAD'] = median_norm_df['water_level_norm'].rolling(window=window_size, min_periods=1, center=center_window).apply(lambda x: np.median(np.abs(x - np.median(x))))
# median_norm_df['MADN'] = median_norm_df['MAD'] / 0.6745
# median_norm_df['M'] = median_norm_df.apply(lambda row: np.abs(row['water_level'] - row['Median']) / row['MADN'] if row['MADN'] != 0 else 0, axis=1)
median_norm_df['M'] = median_norm_df.apply(lambda row: np.abs(row['water_level_norm'] - row['Median']), axis=1)
median_norm_df['prediction'] = median_norm_df.apply(lambda row: True if row['M'] > 3.5 else False, axis=1)
print(metrics.f1_score(median_norm_df['is_outlier'], median_norm_df['prediction']))
median_norm_df['cn'] = median_norm_df.apply(lambda row: get_TP_TN_FP_FN(row['is_outlier'], row['prediction']), axis=1)
fig = px.scatter(median_norm_df, x='timestamp', y='water_level_norm', color='cn',
           title='Water level')
fig.show()
fig = px.scatter(median_norm_df, x='timestamp', y='M', color='cn',
           title='Water level')
fig.show()
median_norm_df

In [ ]:
median_df = df.copy()
window_size = 6
center_window = True
median_df['Median'] = median_df['water_level'].rolling(window=window_size, min_periods=1, center=center_window).median()
# median_norm_df['MAD'] = median_norm_df['water_level_norm'].rolling(window=window_size, min_periods=1, center=center_window).apply(lambda x: np.median(np.abs(x - np.median(x))))
# median_norm_df['MADN'] = median_norm_df['MAD'] / 0.6745
# median_norm_df['M'] = median_norm_df.apply(lambda row: np.abs(row['water_level'] - row['Median']) / row['MADN'] if row['MADN'] != 0 else 0, axis=1)
median_df['M'] = median_df.apply(lambda row: np.abs(row['water_level'] - row['Median']), axis=1)
median_df['prediction'] = median_df.apply(lambda row: True if row['M'] > 7.6 else False, axis=1)
print(metrics.f1_score(median_df['is_outlier'], median_df['prediction']))
median_df['cn'] = median_df.apply(lambda row: get_TP_TN_FP_FN(row['is_outlier'], row['prediction']), axis=1)
fig = px.scatter(median_df, x='timestamp', y='water_level', color='cn',
           title='Water level')
fig.show()
fig = px.scatter(median_df, x='timestamp', y='M', color='cn',
           title='Water level')
fig.show()
median_df

In [ ]:
z_score_df = df.copy()
window_size = 10
center_window = True
z_score_df['mean'] = z_score_df['water_level'].rolling(window=window_size, min_periods=1, center=center_window).mean()
z_score_df['std'] = z_score_df['water_level'].rolling(window=window_size, min_periods=1, center=center_window).std()
z_score_df['z'] = z_score_df.apply(lambda row: np.abs(row['water_level'] - row['mean'])/row['std'], axis=1)
z_score_df['prediction'] = z_score_df.apply(lambda row: True if row['z'] > 2.5 else False, axis=1)
print(metrics.f1_score(z_score_df['is_outlier'], z_score_df['prediction']))
z_score_df['cn'] = z_score_df.apply(lambda row: get_TP_TN_FP_FN(row['is_outlier'], row['prediction']), axis=1)
fig = px.scatter(z_score_df, x='timestamp', y='water_level', color='cn',
           title='Water level')
fig.show()
fig = px.scatter(z_score_df, x='timestamp', y='z', color='cn',
           title='Water level')
fig.show()

z_score_df

In [ ]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
z_score_norm_df = df.copy()
z_score_norm_df['water_level_norm'] = scaler.fit_transform(z_score_norm_df[['water_level']])


window_size = 10
center_window = True
z_score_norm_df['mean'] = z_score_norm_df['water_level_norm'].rolling(window=window_size, min_periods=1, center=center_window).mean()
z_score_norm_df['std'] = z_score_norm_df['water_level_norm'].rolling(window=window_size, min_periods=1, center=center_window).std()
z_score_norm_df['z'] = z_score_norm_df.apply(lambda row: np.abs(row['water_level_norm'] - row['mean'])/row['std'], axis=1)
z_score_norm_df['prediction'] = z_score_norm_df.apply(lambda row: True if row['z'] > 2.5 else False, axis=1)
print(metrics.f1_score(z_score_norm_df['is_outlier'], z_score_norm_df['prediction']))
z_score_norm_df['cn'] = z_score_norm_df.apply(lambda row: get_TP_TN_FP_FN(row['is_outlier'], row['prediction']), axis=1)
fig = px.scatter(z_score_norm_df, x='timestamp', y='water_level_norm', color='cn',
           title='Water level')
fig.show()
fig = px.scatter(z_score_norm_df, x='timestamp', y='z', color='cn',
           title='Water level')
fig.show()

z_score_norm_df

In [ ]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
z_score_diff_df = df.copy()
# z_score_diff_df['water_level_norm'] = scaler.fit_transform(z_score_diff_df[['water_level']])
z_score_diff_df['water_level_delta'] = z_score_diff_df['water_level'].diff(periods=1).fillna(0)

window_size = 10
center_window = True
z_score_diff_df['mean'] = z_score_diff_df['water_level_delta'].rolling(window=window_size, min_periods=1, center=center_window).mean()
z_score_diff_df['std'] = z_score_diff_df['water_level_delta'].rolling(window=window_size, min_periods=1, center=center_window).std()
z_score_diff_df['z'] = z_score_diff_df.apply(lambda row: np.abs(row['water_level_delta'] - row['mean'])/row['std'], axis=1)
z_score_diff_df['prediction'] = z_score_diff_df.apply(lambda row: True if row['z'] > 2.5 else False, axis=1)
print(metrics.f1_score(z_score_diff_df['is_outlier'], z_score_diff_df['prediction']))
z_score_diff_df['cn'] = z_score_diff_df.apply(lambda row: get_TP_TN_FP_FN(row['is_outlier'], row['prediction']), axis=1)
fig = px.scatter(z_score_diff_df, x='timestamp', y='water_level_delta', color='cn',
           title='Water level')
fig.show()
fig = px.scatter(z_score_diff_df, x='timestamp', y='z', color='cn',
           title='Water level')
fig.show()

z_score_diff_df

In [ ]:
def get_z_score(X: np.ndarray, window: int = None,
                center_window: bool = False) -> np.ndarray:
    if window is None:
        return (X - X.mean()) / X.std()
    else:
        # https://stackoverflow.com/questions/47164950/compute-rolling-z-score-in-pandas-dataframe
        x = pd.Series(X.reshape(-1))
        r = x.rolling(window=window, center=center_window)
        m = r.mean().shift(1)
        s = r.std(ddof=0).shift(1)
        z = (x-m)/s
        return z
        # tmp_df = pd.DataFrame({'X': X.reshape(-1)})
        #
        # return tmp_df['X'].rolling(window=window, min_periods=1,
        #                             center=center_window).apply(
        #     lambda x: (x - np.mean(x)) / np.std(x)).to_numpy().reshape(-1, 1)


In [ ]:
def get_delta_z_score(X: np.ndarray, window: int = None,
                center_window: bool = False) -> np.ndarray:
    reshaped_X = X.reshape(-1)
    diff_X = np.diff(reshaped_X, prepend=[reshaped_X[0]])
    if window is None:
        return (diff_X - diff_X.mean()) / diff_X.std()
    else:
        # https://stackoverflow.com/questions/47164950/compute-rolling-z-score-in-pandas-dataframe
        x = pd.Series(diff_X)
        r = x.rolling(window=window, center=center_window)
        m = r.mean().shift(1)
        s = r.std(ddof=0).shift(1)
        z = (x-m)/s
        return z

In [ ]:
def get_mad_z_score(X: np.ndarray, window: int = None,
                center_window: bool = False) -> np.ndarray:
    reshaped_X = X.reshape(-1)
    diff_X = np.diff(reshaped_X, prepend=[reshaped_X[0]])
    if window is None:
        return (diff_X - diff_X.mean()) / diff_X.std()
    else:
        # https://stackoverflow.com/questions/47164950/compute-rolling-z-score-in-pandas-dataframe
        x = pd.Series(diff_X)
        r = x.rolling(window=window)
        m = r.mean().shift(1)
        s = r.std(ddof=0).shift(1)
        z = (x-m)/s
        return z

In [ ]:
def threshold_outlier_prediction(X, y, window, center_window,
                                 method, thresh_start, thresh_stop,
                                 thresh_num):
    thresholds = np.linspace(thresh_start, thresh_stop, thresh_num)
    if method in ['mean', 'median', 'mad']:
        x_hat = get_x_hat(X, method, window, center_window)
    scores = []
    for threshold in thresholds:
        if method in ['mean', 'median', 'mad']:
            y_pred = np.where(np.abs(X - x_hat) > threshold, 1, 0)
        elif method == 'z-score':
            z_score = get_z_score(X, window, center_window)
            y_pred = np.where(z_score > threshold, 1, 0)
        elif method == 'delta-z-score':
            z_score = get_delta_z_score(X, window, center_window)
            y_pred = np.where(z_score > threshold, 1, 0)
        else:
            raise ValueError(f'Method ({method}) not supported')
        # https://stackoverflow.com/questions/33275461/specificity-in-scikit-learn
        tn, fp, fn, tp = metrics.confusion_matrix(y, y_pred).ravel()
        scores.append({'method': method,
                       'f1': metrics.f1_score(y, y_pred, zero_division=0),
                       'precision': metrics.precision_score(y, y_pred, zero_division=0),
                       'recall': metrics.recall_score(y, y_pred,
                                              zero_division=0),
                       'accuracy': metrics.accuracy_score(y, y_pred),
                       'sensitivity': tp / (tp + fn) if tp + fn > 0 else 0,
                       'specificity': tn / (tn + fp) if tn + fp > 0 else 0,
                       'threshold': threshold,
                       'window_size': window,
                       'center_window': center_window,
                       'percentage_outlier_truth': len(y[y == 1]) / len(y),
                       'percentage_outlier_pred': len(y_pred[y_pred == 1]) /
                                                  len(y_pred)
                       # 'pred': y_pred,
                       # 'truth': y
                       })
    return scores
    # return {'pred': y_pred, 'truth': y}